# Calculate Q-Rookley

- Input data "20172022_processed_1_3_4.csv", from 2017/7/1 to 2022/12/31, same as used in Figlewski

- Use 500 rolling window for P density (when calculating EPK)

- Use logreturn instead of log+1

- Use 
```
r.source('Q_Rookley_main_3.R')
```
and
```
'EPK_library_1.r'
```
to calculate Q_Rookley, along with 
```
get_btc_prices_2015_2022
```
for physical density.

- Interest rate: 0

- Moneyness range is [min moneyness, max moneyness]

- Bandwidth 0.3

- tau=3

In [1]:
import platform
plat = platform.system()
import locale
if plat == 'Darwin':
    print('Using Macos Locale')
    locale.setlocale(locale.LC_ALL, 'en_US.UTF-8')
else:
    locale.setlocale(locale.LC_ALL, 'en_US.utf8')
import datetime
import pandas as pd
import sys
import matplotlib.pyplot as plt
import csv
import gc
import math
import numpy as np
import os
import pdb
import pickle
import statsmodels.api as sm
import time


import rpy2.robjects.packages as rpackages
from rpy2 import robjects

from scipy import stats
from scipy.integrate import simps
from scipy import interpolate

from src.helpers import save_dict, load_dict
from src.brc import BRC
from src.strategies import IronCondor
from src.quandl_data import get_btc_prices_2015_2022

from numpy.lib.function_base import insert

from statsmodels.nonparametric.kernel_regression import KernelReg as nadarajawatson

from sklearn.neighbors import KernelDensity

from pathlib import Path

def filter_sub(_df,  mindate, maxdate, tau):
    # Subset

    # Only calls, tau in [0, 0.25] and fix one day (bc looking at intra day here)
    # (_df['is_call'] == 1) & --> Dont need to filter for calls because that happens in the R script
    # Also need to consider put-call parity there
    sub = _df[(_df['date'] >= mindate) & (_df['date'] <= maxdate) & (_df['moneyness'] >= 0.5) & (_df['moneyness'] < 2) &(_df['mark_iv'] > 0)]# &

    if tau > 0:
        sub = sub[sub['tau'] == tau]

    nrows = sub.shape[0]
    if nrows == 0:
        raise(ValueError('Sub is empty'))
   
    sub['moneyness'] = round(sub['moneyness'], 3)
    sub['underlying_price'] = round(sub['underlying_price'], 2)

    sub = sub.drop_duplicates()
    
    print(sub.describe())

    if nrows > 50000:
        print('large df, subsetting')
        sub = sub.sample(10000)
        print(sub.describe())

    return sub

def prepare_confidence_band_data(df):

            # Old
                # Save for Confidence Band 
                    # Column 1 - Day
                    # Column 2 - Month
                    # Column 3 - Year
                    # Column 4 - Call Indicator
                    # Column 5 - Time Maturity in Days
                    # Column 6 - Strike
                    # Column 7 - IV
                    # Column 8 - Spot
                    # Column 9 - Risk Free Rate
                    # Column 10 - 
                    # Column 11 - Forward
                # 3	1	1997	0	49	3025	165.8	2861.706	0.031465	0.150026951	2863.26
                # Day Month Year Put Days Strike IV     Spot         Risk Free    Tau in Days (255)       Forward

    """
    # Mapping Table for Input

    # Column ... X
    # 1 - date
    # 2 - IV
    # 3 - 1 for Call, 0 for Put
    # 4 - Tau 
    # 5 - Strike
    # 6 - assigned meanwhile as put2call[,6]+ put2call[,7] -  put2call[,5]*exp(- mean(put2call[,8])* tau);
    # 7 - Spot
    # 8 - Probably Interest Rate
    # 9 - assigned meanwhile Moneyness: Spot/Strike
    """
    b = df[['date', 'mark_iv', 'putcall', 'tau', 'K', 'underlying_price', 'interest_rate', 'moneyness', 'instrument_price']]
    b['placeholder'] = 0
    b = b.reset_index(drop=True)
    # b['interest_rate'] = 0.00
    b['forward'] = 1

    # Reorder
    df_c = b[['date', 'mark_iv', 'putcall', 'tau', 'K', 'instrument_price', 'underlying_price', 'interest_rate', 'moneyness']]

    unique_maturities = df.days_to_maturity.unique()[0]
    fname = str('confidence_band_input_') + str(unique_maturities) + str('.csv')
    df_c.to_csv(fname, index = False)
    return fname

def bootstrap(conf_fname, phys_fname, rdate, tau, simmethod, r, out_dir, bw, lower, upper):
                            
    try:
        # MAKE SURE TO USE DIFFERENT 2ND INPUT FOR SP500!!
        moneyness, spd, epk, epk_lo, epk_up, logret, spd_logret, epk_logret, epk_logret_lo, epk_logret_up, epk_BS, tau, volas, spd_lo, spd_up, cdf_m, cdf_ret= r.bootstrap_epk(robjects.StrVector([conf_fname]), 
                                      robjects.StrVector([phys_fname]),
                                      robjects.StrVector(rdate),
                                      robjects.StrVector([out_dir]),
                                      robjects.FloatVector([bw]),
                                      robjects.FloatVector([lower]),
                                      robjects.FloatVector([upper])
                                     )
        # Can recover PD here as SPD/EPK
        spd_df = pd.DataFrame({'m': moneyness,
                               'spdy': spd,
                               'spdy_up': spd_up,
                               'spdy_dn': spd_lo,
                               'epk': epk,
                               'ret': logret,
                               'spd_ret': spd_logret,
                               'cb_ret_up': epk_logret_up,
                               'cb_ret_dn': epk_logret_lo,
                               'epk_ret': epk_logret,
                               'volatility': volas,
                               'epk_up': epk_up,
                               'epk_dn': epk_lo,
                               'cdf_m': cdf_m,
                               'cdf_ret': cdf_ret})

        return spd_df
    
    except Exception as e:
        print('Sim failed, proceeding with the next one... - ', simmethod)
        print('exception: ', e)
        
# Initiate R Objects
base = rpackages.importr("base") 
r = robjects.r
r.source('src/confidence_bands.R')
r.source('src/Q_Rookley_main_3.R')

# BTC prices
tdat = get_btc_prices_2015_2022()
tdat[::-1].to_csv('Data/BTC_USD_Quandl_2015_2022.csv', index = False)

bw_range = np.array([0.3])
r_bandwidth = bw_range[0]

simmethod = ['oldschool']

df = pd.read_csv('Data/20172022_processed_1_3_4.csv')
interest_rate_data = pd.read_csv('Data/IR_daily.csv')
interest_rate_data = interest_rate_data.rename(columns={'index': 'date','DTB3': 'interest_rate'})

df1=df[df['tau']==3]
dates=df1['date'].unique()
#df1=df[df['date']>=dates[9]]
#dates = df1['date'].unique()

dates1 = dates

error_i = []
for i0 in range(dates1.size):
    df2 = df1[df1['date']==dates1[i0]]
    
    curr_day = datetime.datetime.strptime(dates1[i0],'%Y-%m-%d')
    curr_day_starttime = curr_day.replace(hour = 0, minute = 0, second = 0, microsecond = 0)
    curr_day_endtime = curr_day.replace(hour = 23, minute = 59, second = 59, microsecond = 0)
    print(curr_day)

    df3 = pd.merge(df2, interest_rate_data, on='date', how='left')
    

    df3['interest_rate'] = 0
    df3['days_to_maturity'] = df3['tau']
    df3['tau'] = df3['tau']/365
    df3['underlying_price'] = df3['BTC_price']
    df3['instrument_price'] = df3['option_price']
    df3['putcall'][df3['putcall']=='C']=1
    df3['putcall'][df3['putcall']=='P']=0
    
    df_1 = df3[['date','BTC_price', 'K', 'interest_rate', 'tau', 'putcall', 'IV',  'moneyness',
                'days_to_maturity',  'underlying_price', 'instrument_price']]
    df_1['mark_iv']=df_1['IV']/100
    
    df_1.to_csv('Results/option_' + datetime.datetime.strftime(curr_day_starttime, '%Y%m%d') + '.csv')
    
    conf_fname = prepare_confidence_band_data(df_1)
    
    rdate = base.as_Date(curr_day.strftime('%Y-%m-%d'))
    rdate_f = base.format(rdate, '%Y-%m-%d')
    
    tau = df['tau'].unique()[0]
    
    spd_btc = bootstrap(conf_fname, 'Data/BTC_USD_Quandl_2015_2022.csv', rdate_f, tau, simmethod, r, 
                                     'Results/Rookley_Q_CB_1722_1_2_5_1_ttm3', r_bandwidth, df_1['moneyness'].min(), df_1['moneyness'].max())
    
    try :
        
        spd_btc.to_csv('Results/Rookley_Q_CB_1722_1_2_5_1_ttm3/btc_pk_'  + str(curr_day_starttime.__format__('%Y-%m-%d')) +'_bw_' + str(r_bandwidth) +  '.csv')
        
        print(spd_btc)
        
    except Exception as e:
        error_i.append(i0)

Using Macos Locale


/opt/anaconda3/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:7: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import (to_datetime, Int64Index, DatetimeIndex, Period,
/opt/anaconda3/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:7: FutureWarning: pandas.Float64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import (to_datetime, Int64Index, DatetimeIndex, Period,
R[write to console]: 
Attaching package: ‘matlab’


R[write to console]: The following object is masked from ‘package:stats’:

    reshape


R[write to console]: The following objects are masked from ‘package:utils’:

    find, fix


R[write to console]: The following object is masked from ‘package:base’:

    sum


R[write to console]: KernSmooth 2.23 loaded
Copyright M. P. Wand 1997-2009

2017-07-25 00:00:00


/var/folders/_7/3860x3293tn4h2dlrp5_t7_h0000gn/T/ipykernel_11189/2166193958.py:197: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['putcall'][df3['putcall']=='C']=1
/var/folders/_7/3860x3293tn4h2dlrp5_t7_h0000gn/T/ipykernel_11189/2166193958.py:198: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['putcall'][df3['putcall']=='P']=0
/var/folders/_7/3860x3293tn4h2dlrp5_t7_h0000gn/T/ipykernel_11189/2166193958.py:202: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyda

[1] "bandwidth: 0.3"
[1] "test no arbitrage condition"
[1] 44.694713  4.722982 66.258718
               [,1]      [,2]         [,3]         [,4]
sigmas -0.245012332 0.3853422 10.265257420 -83.60586182
       -0.240848412 0.4254759  9.896737149 -81.77576989
       -0.236701758 0.4641659  9.536097492 -79.96084930
       -0.232572228 0.5014417  9.183295761 -78.16133112
       -0.228459681 0.5373324  8.838287397 -76.37744274
       -0.224363978 0.5718672  8.501025982 -74.60940774
       -0.220284981 0.6050752  8.171463246 -72.85744564
       -0.216222555 0.6369856  7.849549074 -71.12177181
       -0.212176565 0.6676273  7.535231528 -69.40259720
       -0.208146880 0.6970292  7.228456853 -67.70012825
       -0.204133367 0.7252201  6.929169500 -66.01456667
       -0.200135899 0.7522288  6.637312142 -64.34610932
       -0.196154347 0.7780837  6.352825698 -62.69494798
       -0.192188584 0.8028134  6.075649350 -61.06126929
       -0.188238487 0.8264461  5.805720574 -59.44525449
       -0.18430

...

[1] 44.694713  4.722982 66.258718
                [,1]      [,2]        [,3]        [,4]
sigmas -0.1899247130 1.0452896 -6.97890059  43.8957478
       -0.1867177724 1.0273331 -6.87121539  43.8021774
       -0.1835210835 1.0096477 -6.76366482  43.7074342
       -0.1803345808 0.9922331 -6.65624788  43.6114700
       -0.1771581997 0.9750889 -6.54896388  43.5142374
       -0.1739918761 0.9582147 -6.44181244  43.4156899
       -0.1708355464 0.9416101 -6.33479345  43.3157819
       -0.1676891478 0.9252748 -6.22790707  43.2144686
       -0.1645526179 0.9092086 -6.12115377  43.1117060
       -0.1614258952 0.8934112 -6.01453425  43.0074508
       -0.1583089184 0.8778821 -5.90804948  42.9016603
       -0.1552016269 0.8626213 -5.80170070  42.7942928
       -0.1521039608 0.8476285 -5.69548938  42.6853069
       -0.1490158606 0.8329033 -5.58941724  42.5746619
       -0.1459372674 0.8184456 -5.48348624  42.4623177
       -0.1428681229 0.8042552 -5.37769857  42.3482346
       -0.1398083692 0.7903318 

        0.1968175282 0.9831791  4.02863362   0.6978682
        0.1989970143 0.9942080  4.02855736   0.1621317
        0.2011717605 1.0052255  4.02691205  -0.3753166
        0.2033417875 1.0162272  4.02369600  -0.9143925
        0.2055071156 1.0272085  4.01890799  -1.4550116
        0.2076677653 1.0381650  4.01254727  -1.9970888
        0.2098237565 1.0490922  4.00461357  -2.5405390
        0.2119751095 1.0599857  3.99510710  -3.0852765
        0.2141218441 1.0708410  3.98402853  -3.6312158
        0.2162639801 1.0816537  3.97137897  -4.1782712
        0.2184015372 1.0924195  3.95716001  -4.7263568
        0.2205345348 1.1031340  3.94137369  -5.2753871
        0.2226629925 1.1137929  3.92402246  -5.8252767
        0.2247869294 1.1243921  3.90510924  -6.3759403
        0.2269063648 1.1349271  3.88463735  -6.9272931
        0.2290213177 1.1453939  3.86261053  -7.4792506
        0.2311318070 1.1557883  3.83903294  -8.0317290
        0.2332378515 1.1661061  3.81390913  -8.5846447
        0.

/var/folders/_7/3860x3293tn4h2dlrp5_t7_h0000gn/T/ipykernel_11189/2166193958.py:197: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['putcall'][df3['putcall']=='C']=1
/var/folders/_7/3860x3293tn4h2dlrp5_t7_h0000gn/T/ipykernel_11189/2166193958.py:198: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['putcall'][df3['putcall']=='P']=0
/var/folders/_7/3860x3293tn4h2dlrp5_t7_h0000gn/T/ipykernel_11189/2166193958.py:202: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyda

[1] 44.694713  4.722982 66.258718
                [,1]      [,2]         [,3]        [,4]
sigmas -0.2748896118 1.3167586 -2.099203608 -30.3006742
       -0.2717269611 1.3127859 -2.200759536 -29.2083338
       -0.2685742812 1.3085217 -2.299182494 -28.1219899
       -0.2654315095 1.3039736 -2.394474453 -27.0418733
       -0.2622985839 1.2991495 -2.486638741 -25.9682109
       -0.2591754429 1.2940572 -2.575680014 -24.9012254
       -0.2560620255 1.2887048 -2.661604243 -23.8411355
       -0.2529582713 1.2831002 -2.744418688 -22.7881556
       -0.2498641207 1.2772515 -2.824131875 -21.7424961
       -0.2467795144 1.2711666 -2.900753583 -20.7043629
       -0.2437043935 1.2648537 -2.974294812 -19.6739582
       -0.2406387001 1.2583208 -3.044767768 -18.6514794
       -0.2375823764 1.2515761 -3.112185839 -17.6371200
       -0.2345353654 1.2446278 -3.176563570 -16.6310690
       -0.2314976104 1.2374839 -3.237916643 -15.6335113
       -0.2284690555 1.2301526 -3.296261856 -14.6446274
       -0.2254

        0.1009012932 0.7263748  2.212426546  22.8387808
        0.1030743061 0.7318390  2.263151387  22.5869335
        0.1052426073 0.7374167  2.313088975  22.3317921
        0.1074062171 0.7431059  2.362235741  22.0734938
        0.1095651558 0.7489043  2.410588657  21.8121754
        0.1117194435 0.7548100  2.458145240  21.5479738
        0.1138691002 0.7608208  2.504903546  21.2810257
        0.1160141458 0.7669347  2.550862169  21.0114674
        0.1181546001 0.7731496  2.596020240  20.7394352
        0.1202904826 0.7794634  2.640377422  20.4650652
        0.1224218128 0.7858743  2.683933914  20.1884932
        0.1245486101 0.7923800  2.726690443  19.9098547
        0.1266708937 0.7989788  2.768648266  19.6292850
        0.1287886828 0.8056686  2.809809166  19.3469194
        0.1309019963 0.8124475  2.850175450  19.0628926
        0.1330108532 0.8193135  2.889749949  18.7773392
        0.1351152721 0.8262649  2.928536015  18.4903934
        0.1372152717 0.8332997  2.966537519  18.

In [2]:
print(error_i)

[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 16, 17, 18, 19, 20, 21, 26, 28, 29, 30, 31, 32, 33, 34, 35, 38, 39, 40, 42, 43, 44, 47, 51, 56, 59, 61, 63, 64, 65, 76, 77, 83, 110, 180, 193, 197, 214, 228, 232, 240]
